# Lineære ligningssystemer

Demo af Christian Mikkelstrup og Hans Henrik Hermansen

In [ ]:
from sympy import *
init_printing()

Vi vil gerne løse det lineære ligningssystem

\begin{aligned}
-x_2+x_3=2\\
2x_1+4x_2-2x_3=2\\
3x_1+4x_2+x_3=9\\
\end{aligned}


Dette kan skrives på matrixform $Ax=b$ med koefficientmatrix $A$ givet ved

In [ ]:
A = Matrix([[0,-1,1],[2,4,-2],[3,4,1]])
A

og højreside givet ved

In [ ]:
b = Matrix([2,2,9])
b

Lad os først skrive ligningerne op i SymPy:

In [ ]:
x1,x2,x3 = symbols('x1:4')
eq1 = Eq(-x2 + x3, 2)
eq2 = Eq(2*x1 + 4*x2 - 2*x3, 2)
eq3 = Eq(3*x1 + 4*x2 + x3, 9)
eq1, eq2, eq3

Koefficientmatricen og højresiden for et system af lineære ligninger kan nu findes direkte i SymPy ved kaldet:

In [ ]:
A, b = linear_eq_to_matrix([eq1, eq2, eq3], [x1, x2, x3])
display(A, b)

Det stemmer med hvad vi påstod tidligere. Lad os nu se hvordan vi kan løse ligningssystemet.

**Metode 0:**

Vi har allerede skrevet alle ligningerne op i SymPy, så vi kan bede SymPy om at løse dem:

In [ ]:
linsolve((eq1,eq2,eq3),x1,x2,x3)

**Metode 1:**

Direkte løsning med SymPy ved koefficientmatricen. Der findes flere metoder, men her er præsenteret 2:

In [ ]:
A.gauss_jordan_solve(b)

In [ ]:
linsolve((A,b))

Som har netop én løsning:

\begin{aligned}
(x_1,x_2,x_3)=(4,-1,1).
\end{aligned}

**Metode 2:**

Fuldstændig GaussJordan-elimination kan ordnes med 1 kommando, Reduced Row Echelon Form (rref):

In [ ]:
# Totalmatricen dannes først
T = A.row_join(b)  # or use T = Matrix.hstack(A,b)
T

In [ ]:
T.rref(pivots=False)

Løsningen kan aflæses til 

\begin{aligned}
(x_1,x_2,x_3)=(4,-1,1)
\end{aligned}

Pivots beskriver hvilke kolonner de ledende 1-taller befinder sig i. Hvis vi bare vil have matricen, kan denne sættes til "False". Alternativt kommer outputtet bare ud som:

In [ ]:
T.rref()

**Metode 3:**

Løsning ved brug af GaussJordan elimination, men hvor vi selv udfører hver rækkeoperation:

Første søjle laves ved at bytte række 1 og række 2, hvorefter den nye række 1 ganges med $1/2$. Til sidst lægges $-3$ gange række 1 til række 3:

In [ ]:
T1 = T.elementary_row_op('n<->m', 0, 1)
T2 = T1.elementary_row_op('n->kn', 0, S(1)/2)
T3 = T2.elementary_row_op('n->n+km',2,-3,0)
T1,T2,T3

Så kan vi klare de sidste 2 søjler ved

In [ ]:
T4 = T3.elementary_row_op('n->kn',1,-1)
T5 = T4.elementary_row_op('n->n+km',2,2,1)
T6 = T5.elementary_row_op('n->n+km',0,-2,1)
T4,T5,T6

In [ ]:
T7 = T6.elementary_row_op('n->kn',2,S(1)/2)
T8 = T7.elementary_row_op('n->n+km',0,-1,2)
T9 = T8.elementary_row_op('n->n+km',1,1,2)
T7,T8,T9

Hvor vi her ser, at den sidste matrice er den samme løsning som tidligere.

# Et lineært ligningssystem med flere løsninger

Vi ønsker at løse det inhomogene ligningssystem, hvis koefficientmatrix er givet ved 

In [ ]:
A = Matrix([[1,3,2,4,5],[2,6,4,3,5],[3,8,6,7,6],[4,14,8,10,22]])
A

Hvor **højresiden** er givet ved:

In [ ]:
b = Matrix([9,3,5,32])
b

**Metode 1:**

Løses direkte ved brug af SymPy. Igen er der to metoder:

In [ ]:
A.gauss_jordan_solve(b)

In [ ]:
linsolve((A,b))

Dette læses ved, at $\tau_0$ og $\tau_1$ er de to frie parametre, altså $\tau_0, \tau_1 \in \mathbb{R}$.

**Metode 2:**

Løsning ved fuldstændig reduktion:

Først laves **totalmatricen** ved:

In [ ]:
T = A.row_join(b)
T

In [ ]:
T.rref()

Nu er vi færdige med eliminationen og løsningen kan nemt udregnes (eller direkte aflæses). 

På standard-parameterform er løsningen:

\begin{equation}
\begin{bmatrix}x_1\\x_2\\x_3\\x_4\\x_5
\end{bmatrix}=
\begin{bmatrix}-24\\7\\0\\3\\0
\end{bmatrix}+
\tau_0\begin{bmatrix}-2\\0\\1\\0\\0
\end{bmatrix}+\tau_1\begin{bmatrix}11\\-4\\0\\-1\\1\end{bmatrix}\end{equation}

Her er undladt at sætte "pivots=False" for at vise at som standard beskrives kolonnerne som de ledende 1-taller befinder sig i. Der er ingen ledende 1-taller i søjle 3 og 5, så disse variable (dvs. $x_3$ og $x_5$) bliver vores frie variable (hhv. $\tau_0$ og $\tau_1$).

**Kontrol:**

Vi tjekker at antallet af *frie parametre* (de to vi har) er korrekt:

Antallet af ubekendte er $n=5$, så antallet af frie parametre skulle gerne være lig med $n-\text{A.rank()}$:

In [ ]:
A.rank()

In [ ]:
5-A.rank()

som forventet.

# Når systemet indeholder ubekendte koefficienter

Når ligningssystemet indeholder ukendte koefficienter, kræver det nogle gange lidt mere opmærksomhed. Tilsvarende, kræver det lidt mere arbejde i SymPy.

In [ ]:
a = symbols('a', real=True)
T = Matrix([[1,3,-2,0,0],[1,2,3,-a,-1],[3,7,a+3,-2*a,a-3],[0,1,-5,a**2,a],[1,1,8,-2*a,-2]])
T

Man kunne fristes til bare at spørge SymPy om løsningen direkte:

In [ ]:
T.rref()

Her kan vi se, at vi må kræve at $a\neq 0$. Dog har vi sprunget mange udregninger over (vi har ladet SymPy lave alle udregningerne for os), så det kan være at nogle at disse udregninger SymPy har lavet, kræver at $a$ undgår andre værdier end nul. Vi forsøger derfor at lave GaussJordan-elimination i "hånden" så vi har tjek på alle trin. Vi ordner først den første søjle:

In [ ]:
T1 = T.elementary_row_op('n->n+km',1,-1,0)
T2 = T1.elementary_row_op('n->n+km',2,-3,0)
T3 = T2.elementary_row_op('n->n+km',4,-1,0)
T3

Anden søjle er også ret lige til:

In [ ]:
T4 = T3.elementary_row_op('n->kn',1,-1)
T5 = T4.elementary_row_op('n->n+km',0,-3,1)
T6 = T5.elementary_row_op('n->n+km',2,2,1)
T7 = T6.elementary_row_op('n->n+km',3,-1,1)
T8 = T7.elementary_row_op('n->n+km',4,2,1)
T8

Inden at vi kan gå videre, er det vigtigt at ligge mærke til, at $a-1$ kan gå hen og blive nul. Da vi gerne vil have et ledende 1-tal i tredje række, skal vi dividere med $a-1$, men hvis det er $0$ har vi divideret med $0$ (no good). Dette sker præcis når $a=1$, så lad os antage at $a\neq 1$, og gemme dette specialtilfælde til senere.

Vi fortsætter nu Gauss-Jordan eliminationen:

In [ ]:
T9 = T8.elementary_row_op('n->kn',2,1/(a-1))
T10 = T9.elementary_row_op('n->n+km',1,5,2)
T11 = T10.elementary_row_op('n->n+km',0,-13,2)
T11

Med et ledende 1-tal i fjerde række, kan vi komme til at dividere med $0$ igen. Dette sker præcis når $a^2-a=0$, altså når $a(a-1)=0$. Ved nulreglen må vi kræve at $a$ hverken er nul eller et. Vi tjekker argumentet i SymPy:

In [ ]:
roots(a**2-a,multiple=True)

Da vi allerede har taget højde for det ene special-tilfælde ($a=1$), skal vi bare lave et special-tilfælde for $a=0$. Vi fortsætter altså vores beregninger under antagelsen om at $a\neq0$ og $a\neq1$:

In [ ]:
T12 = T11.elementary_row_op('n->kn',3,1/(a**2-a))
T13 = T12.elementary_row_op('n->n+km',0,3*a,3)
T14 = T13.elementary_row_op('n->n+km',1,-a,3)
T14.simplify()
T14

Vi har nu en fuldstændig reduktion gennemførst, og vi konkluderer:

For $a\neq0$ og $a\neq1$ er der netop én løsning: 

\begin{equation}
\begin{bmatrix}x_1\\x_2\\x_3\\x_4\end{bmatrix}
=\begin{bmatrix}-13\\5\\1\\ \frac{1}{a}\end{bmatrix}
\end{equation}

For specialtilfældet hvor $a=0$ får vi:

In [ ]:
T.subs({a:0}).rref(pivots=False)

Række 4 svarer til at $0=1$. Da dette er umuligt, kan vi konkludere, at:

For $a=0$ har ligningssystemet ingen løsninger.

For specialtilfældet hvor $a=1$ får vi:

In [ ]:
T.subs({a:1}).rref(pivots=False)

Med rank:

In [ ]:
T.subs({a:1}).rank()

Vi kan nu aflæse løsningen eller alternativt bruge SymPy:

In [ ]:
linsolve(T.subs({a:1}))

Vi ser at for $a=1$ har systemet den fuldstændige løsning:

\begin{equation}
\begin{bmatrix}
x_1\\x_2\\x_3\\x_4
\end{bmatrix}=
\begin{bmatrix}-3\\1\\0\\0
\end{bmatrix}+\tau_0
\begin{bmatrix}-13\\5\\1\\0
\end{bmatrix}+\tau_1
\begin{bmatrix}3\\-1\\0\\1
\end{bmatrix}, \;\; \text{hvor } \tau_0, \tau_1 \in \mathbb{R}.\end{equation}

Læg mærke til, at den direkte løsning med $\text{rref()}$ på $T$ i starten af opgaven helt missede at $a=1$ var et specialtilfælde! Man skal altså passe på med bare at springe direkte til løsningen når der er symbolske variable med i matricen!

# MatrixAlgebra

Vi vil regne på følgende matricer:

In [ ]:
A = Matrix([[2,1],[3,0],[7,11]])
B = Matrix([[1,1],[9,3],[-7,-1]])
C = Matrix([[2,1,3],[-6,5,8]])
A,B,C

Vi kan gange matricen $A$ med en konstant ved:

In [ ]:
k = symbols('k',real=True)
k*A

Da $A$ og $B$ er af samme type $\mathbb{R}^{3\times 2}$, kan vi bestemme matrixsummen $A+B$:

In [ ]:
A+B

og vi kan udregne linearkombinationer af matricer. Eksempelvis $3A-5B$:

In [ ]:
3*A-5*B

Da antallet af søjler i $A$ passer med antaller af rækker i $C$, kan vi bestemme matrixproduktet $A \cdot C$

In [ ]:
A*C

Bemærk at for matrixprodukter gælder generelt at $AC \neq CA$:

In [ ]:
display(A*C, C*A)